In [1]:
%matplotlib inline

In [27]:
for item in results:
    print(item)

('so_top_100k_vec_50_win_5_min_2_ep_20', (99, [(99, 0.9356183409690857), (64649, 0.7532026171684265), (88097, 0.7329083681106567)]))
('so_top_100k_vec_50_win_5_min_2_ep_40', (99, [(99, 0.9666736125946045), (81290, 0.7433794736862183), (77995, 0.727575957775116)]))
('so_top_100k_vec_50_win_5_min_2_ep_80', (99, [(99, 0.984288215637207), (8337, 0.7443221211433411), (20935, 0.730827808380127)]))
('so_top_100k_vec_50_win_5_min_5_ep_20', (99, [(99, 0.9539480209350586), (20935, 0.7121366858482361), (77995, 0.6859313249588013)]))
('so_top_100k_vec_50_win_5_min_5_ep_40', (99, [(99, 0.9749147295951843), (8337, 0.7369163632392883), (20935, 0.712823212146759)]))
('so_top_100k_vec_50_win_5_min_5_ep_80', (99, [(99, 0.9749752283096313), (8337, 0.7052820324897766), (77995, 0.6976691484451294)]))
('so_top_100k_vec_50_win_10_min_2_ep_20', (99, [(99, 0.9122547507286072), (2173, 0.7672629356384277), (2054, 0.7566429972648621)]))
('so_top_100k_vec_50_win_10_min_2_ep_40', (99, [(99, 0.9634175300598145), (20

In [29]:
from scipy import spatial

def string_to_tokens(string):
    return gensim.utils.simple_preprocess(string)

string1 = "Can anyone help me figure out how to get time series data to display directly in Tableau?"

string2 = "Does anyone know how to get time series data to display correctly in Tableau?"

string3 = "How can I show a time series data view in Looker?"

string4 = "What sorts of repository do we use for in house python packages?"

v1 = model.infer_vector(string_to_tokens(string1))
v2 = model.infer_vector(string_to_tokens(string2))
v3 = model.infer_vector(string_to_tokens(string3))
v4 = model.infer_vector(string_to_tokens(string4))

print("similarity between v1, v2: " + str(1 - spatial.distance.cosine(v1, v2)))
print("similarity between v1, v3: " + str(1 - spatial.distance.cosine(v1, v3)))
print("similarity between v1, v4: " + str(1 - spatial.distance.cosine(v1, v4)))
print("similarity between v2, v3: " + str(1 - spatial.distance.cosine(v2, v3)))
print("similarity between v2, v4: " + str(1 - spatial.distance.cosine(v2, v4)))
print("similarity between v3, v4: " + str(1 - spatial.distance.cosine(v3, v4)))




similarity between v1, v2: 0.946828305721283
similarity between v1, v3: 0.7044541239738464
similarity between v1, v4: 0.20603083074092865
similarity between v2, v3: 0.7013465762138367
similarity between v2, v4: 0.14238975942134857
similarity between v3, v4: 0.13046894967556


In [2]:
import csv
import os
import gensim
import logging
import smart_open
from bs4 import BeautifulSoup
from markdown import markdown
import time
import pickle
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

datasets = [
    #"stack_overflow_clean_top_50k",
    "stack_overflow_clean_top_100k",
    #"stack_overflow_clean_top_150k",
    "stack_overflow_clean_top_200k",
    #"stack_overflow_clean_top_250k",
    "stack_overflow_clean_top_300k",
    #"stack_overflow_clean_full"
]

vector_sizes = [
    50, 100, 200
]

window_sizes = [
    5, 10
]

min_count_sizes = [
    2, 5
]

epoch_sizes = [
   20, 40, 80
]

def markdown_to_text(markdown_string):
    """ Converts a markdown string to plaintext """
    html = markdown(markdown_string)


    # extract text
    soup = BeautifulSoup(html, "html.parser")
    text = ''.join(soup.findAll(text=True))

    return text


def get_dataset_path(dataset_name):
    return "data/" + dataset_name + ".csv"

def get_train_corpus(filename):
    return list(read_corpus_csv(filename))

def read_corpus_csv(filename, tokens_only=False):
    with smart_open.open(filename, encoding='utf-8') as f:
        reader = csv.reader(f)
        next(reader, None) # Skip csv header
        for i, row in enumerate(reader):
            tokens = gensim.utils.simple_preprocess(row[11])
            if tokens_only:
                yield tokens
            else:
                yield gensim.models.doc2vec.TaggedDocument(tokens, [i])
                
def check_similarity(model, train_corpus):
    seconds = []
    for i in range(100):
        doc_id = i
        ranks = []
        second_ranks = []

        inferred_vector = model.infer_vector(train_corpus[doc_id].words)
        sims = model.dv.most_similar([inferred_vector], topn=len(model.dv))

        rank = [docid for docid, sim in sims].index(doc_id)
        ranks.append(rank)

        second_ranks.append(sims[1])

        seconds.append((i, sims[:3]))
    
    return max(seconds)

#         print('Document ({}): «{}»\n'.format(doc_id, ' '.join(train_corpus[doc_id].words)))
#         print(u'SIMILAR/DISSIMILAR DOCS PER MODEL %s:\n' % model)
#         for label, index in [('MOST', 0), ('SECOND-MOST', 1), ('MEDIAN', len(sims)//2), ('LEAST', len(sims) - 1)]:
#             print(u'%s %s: «%s»\n' % (label, sims[index], ' '.join(train_corpus[sims[index][0]].words)))
            
         

            


In [3]:
results = []
for dataset in datasets:
    print("pickling results list")
    with open("result_" + dataset + ".pkl", "wb") as fp:   #Pickling
        pickle.dump(results, fp)
    dataset_path = get_dataset_path(dataset)
    train_corpus = get_train_corpus(dataset_path)
    print("train_corpus length: " + str(len(train_corpus)))
    for vector_size in vector_sizes:
        for window_size in window_sizes:
            for min_count_size in min_count_sizes:
                for epoch_size in epoch_sizes:
                    model_name = "so_{}_vec_{}_win_{}_min_{}_ep_{}".format(dataset[21:], vector_size, window_size, min_count_size, epoch_size)
                    print(model_name)
                    model = gensim.models.doc2vec.Doc2Vec(vector_size=vector_size, window=window_size, min_count=min_count_size, epochs=epoch_size)
                    print("building vocab")
                    model.build_vocab(train_corpus)
                    print("training")
                    model.train(train_corpus, total_examples=model.corpus_count, epochs=model.epochs)
                    print("checking similarity")
                    results.append((model_name, check_similarity(model, train_corpus)))
                    print("saving model")
                    model.save("models/" + model_name + ".pkl")

pickling results list


2021-11-18 18:29:02,878 : INFO : Doc2Vec lifecycle event {'params': 'Doc2Vec(dm/m,d50,n5,w5,mc2,s0.001,t3)', 'datetime': '2021-11-18T18:29:02.852065', 'gensim': '4.1.2', 'python': '3.8.3 (default, Jul  2 2020, 11:26:31) \n[Clang 10.0.0 ]', 'platform': 'macOS-10.16-x86_64-i386-64bit', 'event': 'created'}
2021-11-18 18:29:02,883 : INFO : collecting all words and their counts
2021-11-18 18:29:02,884 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags


train_corpus length: 100000
so_top_100k_vec_50_win_5_min_2_ep_20
building vocab


2021-11-18 18:29:03,303 : INFO : PROGRESS: at example #10000, processed 1617823 words (3865629/s), 47555 word types, 0 tags
2021-11-18 18:29:03,752 : INFO : PROGRESS: at example #20000, processed 3410308 words (4152307/s), 87171 word types, 0 tags
2021-11-18 18:29:04,239 : INFO : PROGRESS: at example #30000, processed 5266958 words (3820961/s), 121558 word types, 0 tags
2021-11-18 18:29:04,694 : INFO : PROGRESS: at example #40000, processed 7108076 words (4056288/s), 152785 word types, 0 tags
2021-11-18 18:29:05,144 : INFO : PROGRESS: at example #50000, processed 8916092 words (4024624/s), 182549 word types, 0 tags
2021-11-18 18:29:05,592 : INFO : PROGRESS: at example #60000, processed 10752692 words (4106262/s), 209653 word types, 0 tags
2021-11-18 18:29:06,041 : INFO : PROGRESS: at example #70000, processed 12524741 words (3952345/s), 237073 word types, 0 tags
2021-11-18 18:29:06,474 : INFO : PROGRESS: at example #80000, processed 14296899 words (4099776/s), 262037 word types, 0 tags

training


...

train_corpus length: 200000
so_top_200k_vec_50_win_5_min_2_ep_20


2021-11-19 07:29:10,174 : INFO : collecting all words and their counts
2021-11-19 07:29:10,175 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2021-11-19 07:29:10,591 : INFO : PROGRESS: at example #10000, processed 1617823 words (3898383/s), 47555 word types, 0 tags
2021-11-19 07:29:11,122 : INFO : PROGRESS: at example #20000, processed 3410308 words (3383172/s), 87171 word types, 0 tags
2021-11-19 07:29:11,678 : INFO : PROGRESS: at example #30000, processed 5266958 words (3346550/s), 121558 word types, 0 tags
2021-11-19 07:29:12,195 : INFO : PROGRESS: at example #40000, processed 7108076 words (3569001/s), 152785 word types, 0 tags
2021-11-19 07:29:12,712 : INFO : PROGRESS: at example #50000, processed 8916092 words (3501557/s), 182549 word types, 0 tags
2021-11-19 07:29:13,219 : INFO : PROGRESS: at example #60000, processed 10752692 words (3625351/s), 209653 word types, 0 tags
2021-11-19 07:29:13,711 : INFO : PROGRESS: at example #70000, processed 1252

building vocab
training


2021-11-19 07:29:28,636 : INFO : EPOCH 1 - PROGRESS: at 2.10% examples, 545992 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:29,641 : INFO : EPOCH 1 - PROGRESS: at 4.24% examples, 585342 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:30,646 : INFO : EPOCH 1 - PROGRESS: at 6.27% examples, 603793 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:31,677 : INFO : EPOCH 1 - PROGRESS: at 8.32% examples, 610766 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:32,695 : INFO : EPOCH 1 - PROGRESS: at 10.38% examples, 614856 words/s, in_qsize 6, out_qsize 0
2021-11-19 07:29:33,756 : INFO : EPOCH 1 - PROGRESS: at 12.14% examples, 601133 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:34,757 : INFO : EPOCH 1 - PROGRESS: at 13.70% examples, 588488 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:35,766 : INFO : EPOCH 1 - PROGRESS: at 15.56% examples, 590588 words/s, in_qsize 5, out_qsize 0
2021-11-19 07:29:36,782 : INFO : EPOCH 1 - PROGRESS: at 17.40% examples, 588718 words/s, in_qsize 5,

KeyboardInterrupt: 

In [65]:
model.save('model_top_100k_body_with_tag.pkl')

2021-11-18 14:13:22,366 : INFO : Doc2Vec lifecycle event {'fname_or_handle': 'model_top_100k_body_with_tag.pkl', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2021-11-18T14:13:22.366192', 'gensim': '4.1.2', 'python': '3.8.3 (default, Jul  2 2020, 11:26:31) \n[Clang 10.0.0 ]', 'platform': 'macOS-10.16-x86_64-i386-64bit', 'event': 'saving'}
2021-11-18 14:13:22,372 : INFO : storing np array 'vectors' to model_top_100k_body_with_tag.pkl.wv.vectors.npy
2021-11-18 14:13:22,940 : INFO : storing np array 'syn1neg' to model_top_100k_body_with_tag.pkl.syn1neg.npy
2021-11-18 14:13:23,343 : INFO : not storing attribute cum_table
2021-11-18 14:13:24,669 : INFO : saved model_top_100k_body_with_tag.pkl


In [28]:
model = gensim.models.doc2vec.Doc2Vec.load('models/so_top_100k_vec_50_win_5_min_2_ep_80.pkl')

2021-11-19 16:15:52,529 : INFO : loading Doc2Vec object from models/so_top_100k_vec_50_win_5_min_2_ep_80.pkl
2021-11-19 16:15:53,455 : INFO : loading dv recursively from models/so_top_100k_vec_50_win_5_min_2_ep_80.pkl.dv.* with mmap=None
2021-11-19 16:15:53,459 : INFO : loading wv recursively from models/so_top_100k_vec_50_win_5_min_2_ep_80.pkl.wv.* with mmap=None
2021-11-19 16:15:53,462 : INFO : setting ignored attribute cum_table to None
2021-11-19 16:15:58,291 : INFO : Doc2Vec lifecycle event {'fname': 'models/so_top_100k_vec_50_win_5_min_2_ep_80.pkl', 'datetime': '2021-11-19T16:15:58.291573', 'gensim': '4.1.2', 'python': '3.8.3 (default, Jul  2 2020, 11:26:31) \n[Clang 10.0.0 ]', 'platform': 'macOS-10.16-x86_64-i386-64bit', 'event': 'loaded'}


In [23]:

doc_id = 4
ranks = []
second_ranks = []

inferred_vector = model.infer_vector(train_corpus[doc_id].words)
sims = model.dv.most_similar([inferred_vector], topn=len(model.dv))

rank = [docid for docid, sim in sims].index(doc_id)
ranks.append(rank)

second_ranks.append(sims[1])




print('Document ({}): «{}»\n'.format(doc_id, ' '.join(train_corpus[doc_id].words)))
print(u'SIMILAR/DISSIMILAR DOCS PER MODEL %s:\n' % model)
for label, index in [('MOST', 0), ('SECOND-MOST', 1), ('MEDIAN', len(sims)//2), ('LEAST', len(sims) - 1)]:
    print(u'%s %s: «%s»\n' % (label, sims[index], ' '.join(train_corpus[sims[index][0]].words)))

Document (4): «in ios there is new behaviour for modal view controller when being presented now it not fullscreen by default and when try to slide down the app just dismiss the view controller automatically how can prevent this behaviour and get back to the old fullscreen modal vc thanks»

SIMILAR/DISSIMILAR DOCS PER MODEL Doc2Vec(dm/m,d100,n5,w5,mc2,s0.001,t3):

MOST (4, 0.9782128930091858): «in ios there is new behaviour for modal view controller when being presented now it not fullscreen by default and when try to slide down the app just dismiss the view controller automatically how can prevent this behaviour and get back to the old fullscreen modal vc thanks»

SECOND-MOST (27671, 0.6541153192520142): «in ios we have new modal presentation behavior like this how to change background black color»

MEDIAN (78403, 0.13376352190971375): «let say have tensor input of shape and another tensor inplace of shape and an index_tensor of shape the index_tensor represents places of input where w

In [14]:
a = 99
b = 10362

print('Document ({}): «{}»\n'.format(a, ' '.join(train_corpus[a].words)))
print('Document ({}): «{}»\n'.format(b, ' '.join(train_corpus[b].words)))

Document (99): «just recently took an intermediate programming test and one of the questions got wrong was as follows semicolon is not needed after function declaration true or false chose false and please correct me if wrong because feel like going crazy function declaration is what you write before the definition at the top of the code so the compiler knows the function call before even calling it and function definition is what makes up the function as whole declaration int func definition int func return shouldn the answer to this be false»

Document (10362): «found strange behavior with python in operator in false false thought it because of precedence in false true it okay in false error it also okay but what precedence evaluates the following expression then in false if it because of wrong precedence why it doesn fire an error like if in false in other words what happens under the hood of python with this expression in false»

